In [492]:
import numpy as np
import pandas as pd
from tqdm import tqdm
from sklearn.ensemble import GradientBoostingClassifier
from xgboost import XGBRFClassifier
from catboost import CatBoostClassifier
from sklearn.metrics import accuracy_score
import lightgbm as lgb
from sklearn.ensemble import VotingClassifier
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV

In [493]:
tqdm.pandas()

In [494]:
scorecard = pd.read_csv('match_level_scorecard.csv')

In [495]:
train = pd.read_csv('trainingData.csv')
train.head(1)

match id team1  team1_id  \
0   9331181    Ba     11283   

                                    team1_roster_ids  team2  team2_id  \
0  9373356.0:7857520.0:4232164.0:4566540.0:329940...  Hl Ph     12634   

                                    team2_roster_ids winner  winner_id  \
0  3500958.0:4231751.0:2735081.0:2035102.0:369833...  Hl Ph      12634   

  toss winner  ...    match_dt         lighting  series_name   season  \
0       Hl Ph  ...  2022-10-20  day/night match  Sd Mq Ai Ty  2022/23   

  ground_id team_count_50runs_last15 team_winp_last5  \
0      7398                 1.666667        0.672131   

   team1only_avg_runs_last15  team1_winp_team2_last15  ground_avg_runs_last15  
0                      139.0                    100.0              157.178571  

[1 rows x 23 columns]

In [496]:
bowler = pd.read_csv('bowler.csv')
bowler.head(1)

match id bowler  bowler_id                            bowler_details  \
0   8638034  BV Ss  6718396.0  NZ:Right-hand bat:Right-arm medium-fast:   

   is_bowler_captain  is_bowler_keeper  inning  runs  wicket_count  \
0                0.0               0.0       1    21             0   

   balls_bowled  economy  maiden  dots  Fours  Sixes  wides  noballs  \
0            12     10.5       0   3.0      1      1      3        1   

     match_dt  
0  2021-01-01

In [497]:
print("no of data points = ",len(scorecard))

no of data points =  1689


In [498]:
scorecard.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1689 entries, 0 to 1688
Data columns (total 30 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   match id                1689 non-null   int64  
 1   team1                   1689 non-null   object 
 2   team2                   1689 non-null   object 
 3   winner                  1689 non-null   object 
 4   by                      1689 non-null   object 
 5   win amount              1689 non-null   float64
 6   toss winner             1689 non-null   object 
 7   toss decision           1689 non-null   object 
 8   venue                   1689 non-null   object 
 9   city                    1511 non-null   object 
 10  match_dt                1689 non-null   object 
 11  lighting                1689 non-null   object 
 12  series_name             1689 non-null   object 
 13  season                  1689 non-null   object 
 14  ground_id               1689 non-null   

In [499]:
batsman = pd.read_csv('Batsman.csv')
batsman.head(1)

match id batsman  batsman_id                           batsman_details  \
0   8638034   KD Ce   7907451.0  NZ:Right-hand bat:Right-arm medium-fast:   

   is_batsman_captain  is_batsman_keeper  inning  runs  balls_faced  \
0                 0.0                0.0       1     7            5   

   over_faced_first  ... out_by_bowler out_by_fielder  bowler_id  \
0               1.1  ...         JS Nm          TM Jn  2486896.0   

                            bowler_details is_bowler_keeper  \
0  NZ:Left-hand bat:Right-arm medium-fast:              0.0   

   is_bowler_captain  strike_rate  Fours  Sixes    match_dt  
0                0.0        140.0    1.0    NaN  2021-01-01  

[1 rows x 21 columns]

TrainingData:
Roster columns (Batsman and Bowler Dataset)

Match Level:
Probabiltiy of winning batting first or bowling first team in last few matches on that particualr ground nad if toss winner is equal to grater probability --> team label

inning 1(runs,wicket) and inning2(runs,wicket) --> e.g. if the avg inning 1 runs scored by batting first team is greater than the ground avg runs then the team label must be there in the column to signify it's win otherwise other team's label should be there 

Batsman Dataset:
AVG. strike rate - avg strike rates of both the teams from team roster ids (last few matches)
AVG. runs scored by batsman of both the teams (last few matches)

Bowler Dataset:
wicket count by a bowler in last few matches
avg economy by a bowler in last few mathes

In [500]:
test = pd.read_csv('test_data.csv')
test.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'toss winner', 'toss decision', 'venue',
       'city', 'match_dt', 'lighting', 'series_name', 'season', 'ground_id',
       'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15'],
      dtype='object')

In [501]:
scorecard.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1689 entries, 0 to 1688
Data columns (total 30 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   match id                1689 non-null   int64  
 1   team1                   1689 non-null   object 
 2   team2                   1689 non-null   object 
 3   winner                  1689 non-null   object 
 4   by                      1689 non-null   object 
 5   win amount              1689 non-null   float64
 6   toss winner             1689 non-null   object 
 7   toss decision           1689 non-null   object 
 8   venue                   1689 non-null   object 
 9   city                    1511 non-null   object 
 10  match_dt                1689 non-null   object 
 11  lighting                1689 non-null   object 
 12  series_name             1689 non-null   object 
 13  season                  1689 non-null   object 
 14  ground_id               1689 non-null   

In [502]:
batsman.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24483 entries, 0 to 24482
Data columns (total 21 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   match id            24483 non-null  int64  
 1   batsman             24483 non-null  object 
 2   batsman_id          24483 non-null  float64
 3   batsman_details     24483 non-null  object 
 4   is_batsman_captain  24483 non-null  float64
 5   is_batsman_keeper   24483 non-null  float64
 6   inning              24483 non-null  int64  
 7   runs                24483 non-null  int64  
 8   balls_faced         24483 non-null  int64  
 9   over_faced_first    24483 non-null  float64
 10  wicket kind         19155 non-null  object 
 11  out_by_bowler       19155 non-null  object 
 12  out_by_fielder      13838 non-null  object 
 13  bowler_id           18128 non-null  float64
 14  bowler_details      18128 non-null  object 
 15  is_bowler_keeper    18698 non-null  float64
 16  is_b

In [503]:
print("null count = ",batsman['strike_rate'].isnull().value_counts(),',',batsman['runs'].isnull().value_counts())

null count =  strike_rate
False    24474
True         9
Name: count, dtype: int64 , runs
False    24483
Name: count, dtype: int64


Filling null values of important columns in scorecard

In [504]:
batsman['strike_rate'].fillna(0,inplace = True)

/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/1502080407.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  batsman['strike_rate'].fillna(0,inplace = True)


In [505]:
batsman['Fours'].fillna(0,inplace=True)
batsman['Sixes'].fillna(0,inplace=True)

/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/358147324.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  batsman['Fours'].fillna(0,inplace=True)
/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/358147324.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves 

NO null values in important columns

In [506]:
batsman['Fours'].isnull().value_counts()

Fours
False    24483
Name: count, dtype: int64

In [507]:
bowler.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18539 entries, 0 to 18538
Data columns (total 18 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   match id           18539 non-null  int64  
 1   bowler             18539 non-null  object 
 2   bowler_id          18539 non-null  float64
 3   bowler_details     18539 non-null  object 
 4   is_bowler_captain  18539 non-null  float64
 5   is_bowler_keeper   18539 non-null  float64
 6   inning             18539 non-null  int64  
 7   runs               18539 non-null  int64  
 8   wicket_count       18539 non-null  int64  
 9   balls_bowled       18539 non-null  int64  
 10  economy            18539 non-null  float64
 11  maiden             18539 non-null  int64  
 12  dots               18539 non-null  float64
 13  Fours              18539 non-null  int64  
 14  Sixes              18539 non-null  int64  
 15  wides              18539 non-null  int64  
 16  noballs            185

In [508]:
Last_n_matches = 15

Function to get stats of a player in last n games

In [509]:
def giveLastNgamesPlayer(player_id, date, n, bat_or_bowl):
    '''
    Function to get last n games stats of a player before an input date.
    
    Input-
    1. player_id: id of the player to get historical data.
    2. date: date to look-back and get n games. Stats returned are before this input date.
    3. n: Number of historical games stats to return.
    4. bat_or_bowl: Kind of stats to return. {'bat': batting stats to return, 'bowl': bowling stats to return}
    
    Output-None
    
    Returns- dataframe having bowling/batting stats from last n games of a player before an input date. 
    The results are sorted by date.
    '''
    if bat_or_bowl == 'bat':
        df_topick = batsman
        id_col = 'batsman_id'
    else:
        df_topick = bowler
        id_col = 'bowler_id'
        
    return df_topick[(df_topick['match_dt']<date)&(df_topick[id_col]==float(player_id))].sort_values(by='match_dt', ascending=False).head(n)

Function to get win probability of a team in last n matches

In [510]:
def winpLastn(team_id, date, n):
    '''
    Get a team's win % in last n games. If a team has won 3 game out of their last 5, win% is 60%.
    
    Input-
    1. team_id: ID of the team to get their last n games and winner information from those games.
    2. date: match date from which to get last n historical games.
    3. n: look-back window of games.
    
    Output- None
    
    Returns- Float value denoting win% of the team in last n games.
    '''
    # filter out games with either team1/2_id as input team id, match_dt being before current game's date, sort desc by date, and get top n rows (games)
    df_rel = scorecard[(scorecard['match_dt']<date)&((scorecard['team1_id']==team_id)|(scorecard['team2_id']==team_id))].sort_values(by='match_dt', ascending=False).head(n) 
    win_count = df_rel[df_rel['winner_id']==team_id].shape[0] # count number of rows having winner as the input team
    if win_count == 0:
        return 0
    return round(win_count*100/df_rel.shape[0], 2) # return win% rounded to two decimal points

Function to get a total number of 50s scored by a team in last n matches

In [511]:
def no50sLastn(player_list, date, n):
    '''
    Function to get total number of 50s scored by players in the roster of a team in last n games.
    
    Input-
    1. player_list: ':' separated list of player ids in the roster of a team.
    2. date: match date of the game to calculate this feature.
    3. n: Number of games to look-back and create this feature.
    
    Output-None
    
    Returns- int value denoting sum of 50s scored by all players in the roster.
    '''
    
    player_list = str(player_list).split(':') # split string of ':' separated ids into a list of ids
    res_list = []
    for player in player_list: # loop over each player_id in roster
        df_rel = giveLastNgamesPlayer(player_id=player, date=date, n=n, bat_or_bowl='bat') # getting batting stats from last n games for each player.
        df_rel['gte_50runs'] = np.where(df_rel['runs']>=50, 1, 0) # binary indicator to denote whether the player scored a 50 in the game (runs>=50).
        res_list.append(np.nansum(df_rel['gte_50runs']))# Sum up number of 50s for the player and append to a list. We will do this for all players.
    return np.nansum(res_list)# Sum up values of the list which is sum of 50s by all players in the roster.



In [512]:
def avgStrikeRate(player_list,date,n):
    '''
    Function to get average strike rate of all the players in the team
    '''

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bat') #got the batting stats of a player with player_id = player
        res_list.append(np.nanmean(df_player['strike_rate']))
    return np.nanmean(res_list) #average strike rate of a team

testing above function

In [513]:
player_list,date,n = train['team1_roster_ids'][0],train['match_dt'][0],5
val = avgStrikeRate(player_list,date,n)
print("average_strike_rate = ",val)  #testing done good

average_strike_rate =  78.40466666666667


/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:10: RuntimeWarning: Mean of empty slice
  res_list.append(np.nanmean(df_player['strike_rate']))


In [514]:
def calculate_weighted_average(df,col,col_sort):
    df = df.sort_values(by = col_sort,ascending = False)
    #print(df['match_dt'])
    val = list(df[col].ewm(com = 0.2).mean())
    # val = list(df[col].ewm(com = 2).sum())
    #print(val)
    if len(val):
        return val[-1]
    return 0

Function to calculate weighted average runs

In [515]:
def weighted_Avg_runs(player_list,date,n):
    '''
    Function to get wighted average runs of all the players in the team
    '''

    player_list = str(player_list).split(':')
    #print(len(player_list))
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bat') #got the batting stats of a player with player_id = player
        value = calculate_weighted_average(df_player,'runs','match_dt')
        if value:
            res_list.append(value)
    #print(res_list)
    df = pd.DataFrame(res_list,columns=['val'])
    ans = calculate_weighted_average(df,'val','val')
    return ans

Exponentially moving average calculation 

In [516]:
print("weighted average runs = ",weighted_Avg_runs(player_list,date,10))

weighted average runs =  4.56246642383522


Function to calcualted weighted average wickets

In [517]:
def weighted_Avg_wickets(player_list,date,n):
    '''
    Function to get weighted count of wickets taken by team in last n matches
    '''

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bowl')
        value = calculate_weighted_average(df_player,'wicket_count','match_dt')
        if value:
            res_list.append(value)
    df = pd.DataFrame(res_list,columns=['val'])
    ans = calculate_weighted_average(df,'val','val')
    return ans

In [518]:
print("weighted_Avg_wickets = ",weighted_Avg_wickets(player_list,date,10))

weighted_Avg_wickets =  0.018070719583162066


In [519]:
scorecard.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1689 entries, 0 to 1688
Data columns (total 30 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   match id                1689 non-null   int64  
 1   team1                   1689 non-null   object 
 2   team2                   1689 non-null   object 
 3   winner                  1689 non-null   object 
 4   by                      1689 non-null   object 
 5   win amount              1689 non-null   float64
 6   toss winner             1689 non-null   object 
 7   toss decision           1689 non-null   object 
 8   venue                   1689 non-null   object 
 9   city                    1511 non-null   object 
 10  match_dt                1689 non-null   object 
 11  lighting                1689 non-null   object 
 12  series_name             1689 non-null   object 
 13  season                  1689 non-null   object 
 14  ground_id               1689 non-null   

In [520]:
batsman.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24483 entries, 0 to 24482
Data columns (total 21 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   match id            24483 non-null  int64  
 1   batsman             24483 non-null  object 
 2   batsman_id          24483 non-null  float64
 3   batsman_details     24483 non-null  object 
 4   is_batsman_captain  24483 non-null  float64
 5   is_batsman_keeper   24483 non-null  float64
 6   inning              24483 non-null  int64  
 7   runs                24483 non-null  int64  
 8   balls_faced         24483 non-null  int64  
 9   over_faced_first    24483 non-null  float64
 10  wicket kind         19155 non-null  object 
 11  out_by_bowler       19155 non-null  object 
 12  out_by_fielder      13838 non-null  object 
 13  bowler_id           18128 non-null  float64
 14  bowler_details      18128 non-null  object 
 15  is_bowler_keeper    18698 non-null  float64
 16  is_b

kind of dismissals of a batsman

In [521]:
batsman['wicket kind'].value_counts()

wicket kind
caught               12263
bowled                3323
lbw                   1287
run out               1159
caught and bowled      574
stumped                489
retired hurt            31
hit wicket              20
retired out              6
retired not out          3
Name: count, dtype: int64

In [522]:
def run_catch_out(player_list,match_id):
    field = ["caught","run out","stumped"]
    player_list = player_list.split(':')
    #print(player_list)
    df = batsman
    res = 0
    for player_id in player_list:
        wicket_kind = df[(df['match id'] == match_id)&(df['batsman_id']==float(player_id))]['wicket kind']
        wicket_kind = list(wicket_kind)
        if len(wicket_kind)>0:
            wicket_kind = wicket_kind[0]
        else:
            continue
        if wicket_kind in field:
            res+=1
    return res

In [523]:
def fielding_capapbilty(team_id,date,n):

    #match data of last 'n' matches
    df_rel = scorecard[(scorecard['match_dt']<date)&((scorecard['team1_id']==team_id)|(scorecard['team2_id']==team_id))].head(n).reset_index()
    field_capactiy = 0
    for i in range(len(df_rel)):
        match_id = df_rel['match id'][i]
        player_ids = ""
        if(df_rel['team1_id'][i] != team_id):
            player_ids = df_rel['team2_roster_ids'][i]
        else:
            player_ids = df_rel['team1_roster_ids'][i]
        #print(player_ids)
        field_capactiy += run_catch_out(player_ids,match_id)
    return field_capactiy

In [524]:
team_id,dt,n,match_id = train['team1_id'][0],train['match_dt'][0],5,train['match id'][0]

In [525]:
fielding_capapbilty(team_id,dt,n)

13

toss win match win

In [526]:
def toss(match_id,toss_winner,df):
    if toss_winner == df[df['match id'] == match_id]['team1'].reset_index(drop=True)[0]:
        return 0
    return 1

In [527]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15'],
      dtype='object')

In [528]:
bowler.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18539 entries, 0 to 18538
Data columns (total 18 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   match id           18539 non-null  int64  
 1   bowler             18539 non-null  object 
 2   bowler_id          18539 non-null  float64
 3   bowler_details     18539 non-null  object 
 4   is_bowler_captain  18539 non-null  float64
 5   is_bowler_keeper   18539 non-null  float64
 6   inning             18539 non-null  int64  
 7   runs               18539 non-null  int64  
 8   wicket_count       18539 non-null  int64  
 9   balls_bowled       18539 non-null  int64  
 10  economy            18539 non-null  float64
 11  maiden             18539 non-null  int64  
 12  dots               18539 non-null  float64
 13  Fours              18539 non-null  int64  
 14  Sixes              18539 non-null  int64  
 15  wides              18539 non-null  int64  
 16  noballs            185

Function to get count total wickets in last n matches by a team

In [529]:
def wickets(player_list,date,n):
    '''
    Function to get count of wickets taken by team in last n matches
    '''

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bowl')
        res_list.append(np.nansum(df_player['wicket_count'])) # total dot_balls
    return np.nansum(res_list) #total wicket 1 hall taken by the team

testing above function

In [530]:
wkt = wickets(player_list,date,n)
print("total_wicket taken by team in last n matches = ",wkt)

total_wicket taken by team in last n matches =  18


function to get the number of times the bowler had an economy less than 9 in team

In [531]:
def economy_7_halls(player_list,date,n):

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bowl')
        df_player['less_economy'] = np.where(df_player['economy']<=7,1,0)
        res_list.append(np.nansum(df_player['less_economy'])) # count of less than 7 economy
    return np.nansum(res_list) #avaerage of less than 7 economy

checking the above function

In [532]:
ecnmy = economy_7_halls(player_list,date,n)
print("count of less than 7 economy halls = ",ecnmy)

count of less than 7 economy halls =  11


function to calculate total wides bowled by a team in last n matches

In [533]:
def wides(player_list,date,n):
    '''
    Function to get count of 2 wicket halls by a team in last n matches
    '''

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bowl')
        res_list.append(np.nansum(df_player['wides'])) # 2 wicket halls taken by player in last n matches
    return np.nansum(res_list) #average strike rate of a team

checking the function

In [534]:
wds = wides(player_list,date,n)
print("count of wides = ",wds)

count of wides =  7


function to calculate total no balls bowled by a team in last n mathces

In [535]:
def No_balls(player_list,date,n):

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bowl')
        res_list.append(np.nansum(df_player['noballs'])) # 2 wicket halls taken by player in last n matches
    return np.nansum(res_list) #average strike rate of a team

In [536]:
no_balls = No_balls(player_list,date,n)
print("total_noBalls = ",no_balls)

total_noBalls =  1


functions to calculate total boundaries by a team

In [537]:
def count_of_fours(player_list,date,n):

    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bat')
        res_list.append(np.nansum(df_player['Fours'])) #total fours by the player
    return np.nansum(res_list) #total fours by team

In [538]:
def count_of_sixes(player_list,date,n):
    player_list = str(player_list).split(':')
    res_list = []
    for player in player_list:
        df_player = giveLastNgamesPlayer(player_id=player,date = date,n=n,bat_or_bowl='bat')
        res_list.append(np.nansum(df_player['Sixes'])) #total fours by the player
    return np.nansum(res_list) #total fours by team

cehcking above two functions

In [539]:
boundaries = count_of_fours(player_list,date,n)+count_of_sixes(player_list,date,n)
print("total_boundaries by a team = ",boundaries)

total_boundaries by a team =  40.0


In [540]:
def winpCrossLastn(team1_id, team2_id, date, n):
    '''
    Function to compute team1's win% against team2 from the current game in their past n encounters.
    
    Input-
    1. team1_id: ID of team1 to calculate win% of.
    2. team2_id: ID of team2 to calculate win% against.
    3: date: match date of the current game for which the feature is to be calculated.
    4. n: look-back window of games for both these teams.
    
    Output- None
    
    Returns- Float value denoting team1's win% against team2 in their past n games against each other.
    '''
    # filter out games where either team1_id is input team1 and team2_id is input team2, or where team2_id is input team1 and team1_id is input team2.
    # Also, match date is less than current games's input date, sort desc by date and get top n rows (games)
    df_rel = scorecard[(scorecard['match_dt']<date)&(((scorecard['team1_id']==team1_id)&(scorecard['team2_id']==team2_id))|((scorecard['team1_id']==team2_id)&(scorecard['team2_id']==team1_id)))].sort_values(by='match_dt', ascending=False).head(n)
    win_count = df_rel[df_rel['winner_id']==team1_id].shape[0] # Counting number of rows (games) where winner is input team1.
    if win_count == 0:
        return 0
    return round(win_count*100/df_rel.shape[0], 2) # return Float denoting team1's win% against team2 in past n games rounded to 2 decimal places.

In [541]:
def avgRunsGround(ground_id, date, n):
    '''
    Function to calculate average runs scored in ground/venue.
    
    Input-
    1. ground_id: ID of the ground to calculate the feature for.
    2. date: match date of the current game to calculate the feature for.
    3. n: look-back window of games for the ground.
    
    Output- None
    
    Returns- Average runs scored in the ground.
    '''
    # filter out games with ground_id being the input ground_id and date earlier than current game's input date. Sort desc by date, and select top n rows (games).
    df_rel = scorecard[(scorecard['match_dt']<date)&(scorecard['ground_id']==ground_id)].sort_values(by='match_dt', ascending=False).head(n)
    df_rel['avg_runs_inn'] = (df_rel['inning1_runs']+df_rel['inning2_runs'])/2 # take the mean of inning1_runs and inning2_runs in a separate column.
    return df_rel['avg_runs_inn'].mean() # Return the mean value of the computed column above.

In [542]:
def team1AvgRunsLastn(team_id, date, n):
    '''
    Function to calculate a team's average runs in their last n games.
    
    Input-
    1. team_id: ID of the team to calculate average runs.
    2. date: match date of the current game for which the feature is calculated.
    3. n: look-back window of games for the team.
    
    Output- None
    
    Return- Float value denoting average of runs scored by team1 in their last n games.
    '''
    # filter out games with either team1/2_id as input team_id, match date less than current game's input date, sort desc by date, and top n rows (games) returned
    df_rel = scorecard[(scorecard['match_dt']<date)&((scorecard['team1_id']==team_id)|(scorecard['team2_id']==team_id))].sort_values(by='match_dt', ascending=False).head(n)
    # combine two dataframes - one where input team is batting first, and another one where input team is batting second.
    df_rel = pd.concat([ df_rel[df_rel['team1_bat_inning']==1][['inning1_runs']].rename(columns={'inning1_runs':'runs'}),df_rel[df_rel['team1_bat_inning']==2][['inning2_runs']].rename(columns={'inning2_runs':'runs'}) ] )
    return df_rel['runs'].mean() # return mean of the combined dataframe.

In [543]:
def team2AvgRunsLastn(team_id, date, n):
    '''
    Function to calculate a team's average runs in their last n games.
    
    Input-
    1. team_id: ID of the team to calculate average runs.
    2. date: match date of the current game for which the feature is calculated.
    3. n: look-back window of games for the team.
    
    Output- None
    
    Return- Float value denoting average of runs scored by team1 in their last n games.
    '''
    # filter out games with either team1/2_id as input team_id, match date less than current game's input date, sort desc by date, and top n rows (games) returned
    df_rel = scorecard[(scorecard['match_dt']<date)&((scorecard['team1_id']==team_id)|(scorecard['team2_id']==team_id))].sort_values(by='match_dt', ascending=False).head(n)
    # combine two dataframes - one where input team is batting first, and another one where input team is batting second.
    df_rel = pd.concat([ df_rel[df_rel['team1_bat_inning']==1][['inning2_runs']].rename(columns={'inning2_runs':'runs'}),df_rel[df_rel['team1_bat_inning']==2][['inning1_runs']].rename(columns={'inning1_runs':'runs'}) ] )
    return df_rel['runs'].mean() # return mean of the combined dataframe.

In [544]:
scorecard.columns

Index(['match id', 'team1', 'team2', 'winner', 'by', 'win amount',
       'toss winner', 'toss decision', 'venue', 'city', 'match_dt', 'lighting',
       'series_name', 'season', 'ground_id', 'umpire1', 'umpire2',
       'inning1_runs', 'inning1_wickets', 'inning1_balls', 'inning2_runs',
       'inning2_wickets', 'inning2_balls', 'team1_id', 'team1_roster_ids',
       'team2_id', 'team2_roster_ids', 'series_type', 'winner_id',
       'player_of_the_match_id'],
      dtype='object')

In [545]:
def ratio_of_wins(team_id,match_dt,n):
    #calculate the ratio of wins of team by runs to by wicket
    df = scorecard[(scorecard['match_dt']<match_dt)&((scorecard['team1_id'] == team_id) | (scorecard['team2_id'] == team_id))].head(n).reset_index(drop = True)
    wkt_win = len(df[df['by'] == 'wickets'])
    rn_win = len(df[df['by'] == 'runs'])
    return (1+rn_win)/(1+wkt_win)

checking the functions

In [546]:
team_id,dt,n = train['team1_id'][0],train['match_dt'][0],5
ratio_of_wins(team_id,dt,n)

1.3333333333333333

In [547]:
scorecard['team1_bat_inning'] = np.where( ((scorecard['team1']==scorecard['toss winner'])&(scorecard['toss decision']=='bat'))| ((scorecard['team2']==scorecard['toss winner'])&(scorecard['toss decision']=='field')) , 1, 2)

In [548]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 23 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   match id                   948 non-null    int64  
 1   team1                      948 non-null    object 
 2   team1_id                   948 non-null    int64  
 3   team1_roster_ids           948 non-null    object 
 4   team2                      948 non-null    object 
 5   team2_id                   948 non-null    int64  
 6   team2_roster_ids           948 non-null    object 
 7   winner                     948 non-null    object 
 8   winner_id                  948 non-null    int64  
 9   toss winner                948 non-null    object 
 10  toss decision              948 non-null    object 
 11  venue                      948 non-null    object 
 12  city                       948 non-null    object 
 13  match_dt                   948 non-null    object 

In [549]:
train['team1only_avg_runs_last15'].fillna(train['team1only_avg_runs_last15'].mean(),inplace=True)
train['ground_avg_runs_last15'].fillna(train['ground_avg_runs_last15'].mean(),inplace=True)

/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/3702918245.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  train['team1only_avg_runs_last15'].fillna(train['team1only_avg_runs_last15'].mean(),inplace=True)
/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/3702918245.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the interm

In [550]:
print("team1_avg_runs_null_cnt = ",train['team1only_avg_runs_last15'].isnull().value_counts(),"ground_avg_null_count = ",train['ground_avg_runs_last15'].isnull().value_counts())

team1_avg_runs_null_cnt =  team1only_avg_runs_last15
False    948
Name: count, dtype: int64 ground_avg_null_count =  ground_avg_runs_last15
False    948
Name: count, dtype: int64


No null values in important columns

In [551]:
print("total_number of rows in train dataset = ",len(train))

total_number of rows in train dataset =  948


In [552]:
# Compute average runs scored by team1 in their last 15 games for train data.
train['team2only_avg_runs_last15'] = train.progress_apply(lambda x:team2AvgRunsLastn(x['team2_id'], x['match_dt'], 15), axis=1)

100%|██████████| 948/948 [00:01<00:00, 828.67it/s]


In [553]:
train['team2only_avg_runs_last15'].isnull().value_counts()

team2only_avg_runs_last15
False    926
True      22
Name: count, dtype: int64

keep track of these null values

In [554]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15'],
      dtype='object')

In [555]:
train['team1_avg_strike_rate'] = train.progress_apply(lambda x:avgStrikeRate(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['team2_avg_strike_rate'] = train.progress_apply(lambda x:avgStrikeRate(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

  0%|          | 0/948 [00:00<?, ?it/s]/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:10: RuntimeWarning: Mean of empty slice
  res_list.append(np.nanmean(df_player['strike_rate']))
  2%|▏         | 20/948 [00:00<00:10, 84.60it/s]/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:11: RuntimeWarning: Mean of empty slice
  return np.nanmean(res_list) #average strike rate of a team
  0%|          | 0/948 [00:00<?, ?it/s]/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:10: RuntimeWarning: Mean of empty slice
  res_list.append(np.nanmean(df_player['strike_rate']))
  5%|▌         | 52/948 [00:00<00:09, 93.30it/s] /var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:11: RuntimeWarning: Mean of empty slice
  return np.nanmean(res_list) #average strike rate of a team
100%|██████████| 948/948 [00:10<00:00, 91.56it/s]


In [556]:
train['ratio_team12_strike_rate'] = (1+train['team1_avg_strike_rate'])/(1+train['team2_avg_strike_rate'])
train.drop(['team1_avg_strike_rate','team2_avg_strike_rate'],axis = 1,inplace = True)

In [557]:
train['wicket_team1'] = train.progress_apply(lambda x:wickets(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['wicket_team2'] = train.progress_apply(lambda x:wickets(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:08<00:00, 115.21it/s]


In [558]:
train['wicket_team_ratio'] = (1+train['wicket_team1'])/(1+train['wicket_team2'])
train.drop(['wicket_team1','wicket_team2'],axis = 1,inplace = True)

In [559]:
train['economy_team1'] = train.progress_apply(lambda x:economy_7_halls(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['economy_team2'] = train.progress_apply(lambda x:economy_7_halls(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:09<00:00, 96.19it/s] 


In [560]:
train['economy_team_ratio'] = (1+train['economy_team1'])/(1+train['economy_team2'])
train.drop(['economy_team1','economy_team2'],axis = 1,inplace=True)

In [561]:
train['wides_team1'] =  train.progress_apply(lambda x:wides(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['wides_team2'] =  train.progress_apply(lambda x:wides(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:08<00:00, 118.44it/s]


In [562]:
train['wides'] = (1+train['wides_team1'])/(1+train['wides_team2'])
train.drop(['wides_team1','wides_team2'],axis = 1,inplace=True)

In [563]:
train['noballs_team1'] =  train.progress_apply(lambda x:No_balls(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['noballs_team2'] =  train.progress_apply(lambda x:No_balls(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:08<00:00, 118.37it/s]


In [564]:
train['noballs_ratio'] = (1+train['noballs_team1'])/(1+train['noballs_team2'])
train.drop(['noballs_team1','noballs_team2'],axis = 1,inplace=True)

In [565]:
train['fours_team1'] = train.progress_apply(lambda x:count_of_fours(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['fours_team2'] = train.progress_apply(lambda x:count_of_fours(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

train['six_team1'] = train.progress_apply(lambda x:count_of_sixes(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['six_team2'] = train.progress_apply(lambda x:count_of_sixes(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:10<00:00, 93.30it/s]


In [566]:
train['boundaries_ratio'] = (1+train['fours_team1']+train['six_team1'])/(1+train['fours_team2']+train['six_team2'])
train.drop(['fours_team1','fours_team2','six_team1','six_team2'],axis = 1,inplace = True)

In [567]:
train['team2_winp_last5'] = train.progress_apply(lambda x:winpLastn(x['team1_id'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:00<00:00, 2178.61it/s]


In [568]:
train['toss_win_match_win'] = train.progress_apply(lambda x:toss(x['match id'],x['toss winner'],train),axis = 1)

100%|██████████| 948/948 [00:00<00:00, 5971.96it/s]


In [569]:
train['field_team1'] = train.progress_apply(lambda x:fielding_capapbilty(x['team1_id'],x['match_dt'],Last_n_matches),axis = 1)
train['field_team2'] = train.progress_apply(lambda x:fielding_capapbilty(x['team2_id'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:21<00:00, 44.97it/s]


In [570]:
train['field_ratio'] = (1+train['field_team1'])/(1+train['field_team2'])
train.drop(['field_team1','field_team2'],axis = 1,inplace = True)

In [571]:
train['weighted_runs_team1'] = train.progress_apply(lambda x:weighted_Avg_runs(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['weighted_runs_team2'] = train.progress_apply(lambda x:weighted_Avg_runs(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:10<00:00, 86.72it/s]


In [572]:
train['weighted_avg_runs_ratio'] = (1+train['weighted_runs_team1'])/(1+train['weighted_runs_team2'])
train.drop(['weighted_runs_team1','weighted_runs_team2'],axis = 1,inplace = True)

In [573]:
train['weighted_wickets_team1'] = train.progress_apply(lambda x:weighted_Avg_wickets(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
train['weighted_wickets_team2'] = train.progress_apply(lambda x:weighted_Avg_wickets(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:09<00:00, 104.68it/s]


In [574]:
train['weighted_avg_wickets_ratio'] = (1+train['weighted_wickets_team1'])/(1+train['weighted_wickets_team2'])
train.drop(['weighted_wickets_team1','weighted_wickets_team2'],axis = 1,inplace = True)

In [575]:
train['win_by_team1'] = train.progress_apply(lambda x:ratio_of_wins(x['team1_id'],x['match_dt'],Last_n_matches),axis = 1)
train['win_by_team2'] = train.progress_apply(lambda x:ratio_of_wins(x['team2_id'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 948/948 [00:00<00:00, 1982.72it/s]


In [576]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 37 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   match id                    948 non-null    int64  
 1   team1                       948 non-null    object 
 2   team1_id                    948 non-null    int64  
 3   team1_roster_ids            948 non-null    object 
 4   team2                       948 non-null    object 
 5   team2_id                    948 non-null    int64  
 6   team2_roster_ids            948 non-null    object 
 7   winner                      948 non-null    object 
 8   winner_id                   948 non-null    int64  
 9   toss winner                 948 non-null    object 
 10  toss decision               948 non-null    object 
 11  venue                       948 non-null    object 
 12  city                        948 non-null    object 
 13  match_dt                    948 non

In [577]:
train['team2only_avg_runs_last15'] = train['team2only_avg_runs_last15'].fillna(np.mean(train['team2only_avg_runs_last15']))
train['ratio_team12_strike_rate'] = train['ratio_team12_strike_rate'].fillna(np.mean(train['ratio_team12_strike_rate']))

In [578]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 37 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   match id                    948 non-null    int64  
 1   team1                       948 non-null    object 
 2   team1_id                    948 non-null    int64  
 3   team1_roster_ids            948 non-null    object 
 4   team2                       948 non-null    object 
 5   team2_id                    948 non-null    int64  
 6   team2_roster_ids            948 non-null    object 
 7   winner                      948 non-null    object 
 8   winner_id                   948 non-null    int64  
 9   toss winner                 948 non-null    object 
 10  toss decision               948 non-null    object 
 11  venue                       948 non-null    object 
 12  city                        948 non-null    object 
 13  match_dt                    948 non

Labels made here

In [579]:
def get_labels(team1_id,winner_id):
    if(team1_id == winner_id):
        return 0
    return 1

In [580]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2'],
      dtype='object')

In [581]:
train['labels'] = train.progress_apply(lambda x:get_labels(x['team1_id'],x['winner_id']),axis = 1)

100%|██████████| 948/948 [00:00<00:00, 159277.37it/s]


In [582]:
train_copy = train

In [583]:
train_copy.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2', 'labels'],
      dtype='object')

In [584]:
X = train.drop(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id','labels','wicket_team_ratio','noballs_ratio','wides'],axis = 1)

In [585]:
columns = X.columns

Normalize the dataset

In [586]:
X_norm = (X - X.mean())/(X.max() - X.min())

In [587]:
X_norm = np.array(X)
y = np.array(train_copy['labels'])

In [588]:
print(X_norm.shape,y.shape)

(948, 16) (948,)


In [589]:
gbc = GradientBoostingClassifier()
xgbm = XGBRFClassifier(learning_rate=0.1,max_depth = 5,n_estimators = 10)
cat = CatBoostClassifier(learning_rate=0.1,depth=15,iterations=300)
lgt = lgb.LGBMClassifier(learning_rate=0.001)

In [590]:
X_train,X_val,y_train,y_val = train_test_split(X,y,test_size=0.2)

In [591]:
print(X_train.shape,y_train.shape,X_val.shape,y_val.shape)

(758, 16) (758,) (190, 16) (190,)


In [592]:
param_grid_lgbm = {
    'n_estimators': [100, 200, 300],  # number of trees
    'max_depth': [-1,0,1],           # depth of the trees
    'learning_rate': [0.01,0.02,0.03, 0.04] # learning rate
}

In [593]:
param_grid = {
    'n_estimators': [100, 200, 300],  # number of trees
    'max_depth': [3, 5, 7],           # depth of the trees
    'learning_rate': [0.01, 0.1, 0.2] # learning rate
}

In [594]:
param_grid_cat = {
    'iterations': [100, 200, 300],  # number of trees
    'depth': [3, 5, 7],           # depth of the trees
    'learning_rate': [0.01, 0.1, 0.2] # learning rate
}

In [595]:
cat_grid = GridSearchCV(estimator=cat,param_grid = param_grid_cat,cv=5)

In [596]:
cat_grid.fit(X_train,y_train)

0:	learn: 0.6927052	total: 994us	remaining: 98.5ms
1:	learn: 0.6924555	total: 2.31ms	remaining: 113ms
2:	learn: 0.6922535	total: 2.72ms	remaining: 88ms
3:	learn: 0.6918586	total: 3.11ms	remaining: 74.6ms
4:	learn: 0.6915781	total: 5.22ms	remaining: 99.2ms
5:	learn: 0.6912219	total: 6.15ms	remaining: 96.3ms
6:	learn: 0.6909469	total: 8.17ms	remaining: 109ms
7:	learn: 0.6905861	total: 8.58ms	remaining: 98.7ms
8:	learn: 0.6901674	total: 8.97ms	remaining: 90.7ms
9:	learn: 0.6898154	total: 9.35ms	remaining: 84.1ms
10:	learn: 0.6893662	total: 9.74ms	remaining: 78.8ms
11:	learn: 0.6889422	total: 10ms	remaining: 73.6ms
12:	learn: 0.6886186	total: 10.6ms	remaining: 71.2ms
13:	learn: 0.6882341	total: 15.4ms	remaining: 94.9ms
14:	learn: 0.6879970	total: 16.5ms	remaining: 93.3ms
15:	learn: 0.6875364	total: 17.5ms	remaining: 91.9ms
16:	learn: 0.6871693	total: 18ms	remaining: 87.8ms
17:	learn: 0.6867635	total: 18.7ms	remaining: 85.2ms
18:	learn: 0.6865986	total: 18.9ms	remaining: 80.8ms
19:	learn: 0

89:	learn: 0.4847891	total: 26.5ms	remaining: 2.94ms
90:	learn: 0.4816172	total: 26.8ms	remaining: 2.65ms
91:	learn: 0.4806336	total: 27.1ms	remaining: 2.36ms
92:	learn: 0.4785543	total: 27.4ms	remaining: 2.06ms
93:	learn: 0.4760707	total: 27.6ms	remaining: 1.76ms
94:	learn: 0.4749606	total: 27.8ms	remaining: 1.47ms
95:	learn: 0.4735171	total: 28ms	remaining: 1.17ms
96:	learn: 0.4730226	total: 28.3ms	remaining: 874us
97:	learn: 0.4717840	total: 28.5ms	remaining: 581us
98:	learn: 0.4701499	total: 28.7ms	remaining: 289us
99:	learn: 0.4684628	total: 28.9ms	remaining: 0us
0:	learn: 0.6926168	total: 545us	remaining: 109ms
1:	learn: 0.6917822	total: 928us	remaining: 91.9ms
2:	learn: 0.6911924	total: 1.25ms	remaining: 81.8ms
3:	learn: 0.6907204	total: 1.54ms	remaining: 75.6ms
4:	learn: 0.6902588	total: 1.86ms	remaining: 72.7ms
5:	learn: 0.6897748	total: 2.21ms	remaining: 71.5ms
6:	learn: 0.6893613	total: 2.53ms	remaining: 69.7ms
7:	learn: 0.6889717	total: 2.87ms	remaining: 68.9ms
8:	learn: 0.

GridSearchCV(cv=5,
             estimator=<catboost.core.CatBoostClassifier object at 0x179260cd0>,
             param_grid={'depth': [3, 5, 7], 'iterations': [100, 200, 300],
                         'learning_rate': [0.01, 0.1, 0.2]})

In [643]:
best_cat = CatBoostClassifier(learning_rate=0.01,iterations=300,depth=5)

In [644]:
best_cat.fit(X_train,y_train)

0:	learn: 0.6925673	total: 5.63ms	remaining: 1.68s
1:	learn: 0.6918724	total: 6.67ms	remaining: 993ms
2:	learn: 0.6911880	total: 7.38ms	remaining: 731ms
3:	learn: 0.6902975	total: 8.15ms	remaining: 603ms
4:	learn: 0.6896126	total: 9.19ms	remaining: 542ms
5:	learn: 0.6885561	total: 10ms	remaining: 490ms
6:	learn: 0.6877762	total: 10.9ms	remaining: 455ms
7:	learn: 0.6872066	total: 11.8ms	remaining: 430ms
8:	learn: 0.6865467	total: 12.5ms	remaining: 405ms
9:	learn: 0.6857409	total: 13.3ms	remaining: 385ms
10:	learn: 0.6849659	total: 14ms	remaining: 369ms
11:	learn: 0.6842954	total: 14.8ms	remaining: 355ms
12:	learn: 0.6837898	total: 15.6ms	remaining: 344ms
13:	learn: 0.6827230	total: 16.4ms	remaining: 334ms
14:	learn: 0.6817379	total: 17.9ms	remaining: 341ms
15:	learn: 0.6809410	total: 19ms	remaining: 337ms
16:	learn: 0.6802484	total: 20ms	remaining: 333ms
17:	learn: 0.6795768	total: 21.2ms	remaining: 333ms
18:	learn: 0.6787048	total: 22.1ms	remaining: 327ms
19:	learn: 0.6780288	total: 22

In [599]:
best_cat.get_params()

{'iterations': 300, 'learning_rate': 0.01, 'depth': 5}

In [600]:
xgbm_grid = GridSearchCV(estimator=xgbm,param_grid=param_grid,cv=5)

In [601]:
xgbm_grid.fit(X_train,y_train)

GridSearchCV(cv=5,
             estimator=XGBRFClassifier(base_score=None, booster=None,
                                       callbacks=None, colsample_bylevel=None,
                                       colsample_bytree=None, device=None,
                                       early_stopping_rounds=None,
                                       enable_categorical=False,
                                       eval_metric=None, feature_types=None,
                                       gamma=None, grow_policy=None,
                                       importance_type=None,
                                       interaction_constraints=None,
                                       learning_rate=0.1, max_bin=None,
                                       max_cat_...one,
                                       max_cat_to_onehot=None,
                                       max_delta_step=None, max_depth=5,
                                       max_leaves=None, min_child_weight=None,
                                       missing=nan, monotone_constraints=None,
                                       multi_strategy=None, n_estimators=10,
                                       n_jobs=None, num_parallel_tree=None,
                                       objective='binary:logistic',
                                       random_state=None, ...),
             param_grid={'learning_rate': [0.01, 0.1, 0.2],
                         'max_depth': [3, 5, 7],
                         'n_estimators': [100, 200, 300]})

In [602]:
best_xgbm = xgbm_grid.best_estimator_
best_xgbm.get_params()

{'colsample_bynode': 0.8,
 'learning_rate': 0.2,
 'reg_lambda': 1e-05,
 'subsample': 0.8,
 'objective': 'binary:logistic',
 'base_score': None,
 'booster': None,
 'callbacks': None,
 'colsample_bylevel': None,
 'colsample_bytree': None,
 'device': None,
 'early_stopping_rounds': None,
 'enable_categorical': False,
 'eval_metric': None,
 'feature_types': None,
 'gamma': None,
 'grow_policy': None,
 'importance_type': None,
 'interaction_constraints': None,
 'max_bin': None,
 'max_cat_threshold': None,
 'max_cat_to_onehot': None,
 'max_delta_step': None,
 'max_depth': 5,
 'max_leaves': None,
 'min_child_weight': None,
 'missing': nan,
 'monotone_constraints': None,
 'multi_strategy': None,
 'n_estimators': 100,
 'n_jobs': None,
 'num_parallel_tree': None,
 'random_state': None,
 'reg_alpha': None,
 'sampling_method': None,
 'scale_pos_weight': None,
 'tree_method': None,
 'validate_parameters': None,
 'verbosity': None}

In [603]:
lgt_grid = GridSearchCV(estimator=lgt,param_grid=param_grid,cv=5)

In [604]:
lgt_grid.fit(X_train,y_train)

[LightGBM] [Info] Number of positive: 304, number of negative: 302
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000693 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2112
[LightGBM] [Info] Number of data points in the train set: 606, number of used features: 16
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.501650 -> initscore=0.006601
[LightGBM] [Info] Start training from score 0.006601
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

GridSearchCV(cv=5, estimator=LGBMClassifier(learning_rate=0.001),
             param_grid={'learning_rate': [0.01, 0.1, 0.2],
                         'max_depth': [3, 5, 7],
                         'n_estimators': [100, 200, 300]})

In [605]:
gbc_grid = GridSearchCV(param_grid=param_grid,estimator = gbc,cv = 5)

In [606]:
gbc_grid.fit(X_train,y_train)

KeyboardInterrupt: 

In [ ]:
best_gbc = gbc_grid.best_estimator_

In [ ]:
best_lgt = lgt_grid.best_estimator_

In [ ]:
# Ensemble using VotingClassifier
ensemble_model = VotingClassifier(estimators=[
    ('lgbm', best_lgt),
    ('xgb', best_xgbm),
    ('cat',best_cat),
    ('gbc',best_gbc)
], voting='soft')  # 'soft' voting uses predicted probabilities

ensemble_model.fit(X_train, y_train)

[LightGBM] [Info] Number of positive: 394, number of negative: 364
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000252 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2478
[LightGBM] [Info] Number of data points in the train set: 758, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.519789 -> initscore=0.079197
[LightGBM] [Info] Start training from score 0.079197
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

VotingClassifier(estimators=[('lgbm',
                              LGBMClassifier(learning_rate=0.01, max_depth=5,
                                             n_estimators=200)),
                             ('xgb',
                              XGBRFClassifier(base_score=None, booster=None,
                                              callbacks=None,
                                              colsample_bylevel=None,
                                              colsample_bytree=None,
                                              device=None,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None,
                                              feature_types=None, gamma=None,
                                              grow_policy=None,
                                              importan...
                                              max_delta_step=None, max_depth=3,
                                              max_leaves=None,
                                              min_child_weight=None,
                                              missing=nan,
                                              monotone_constraints=None,
                                              multi_strategy=None,
                                              n_estimators=100, n_jobs=None,
                                              num_parallel_tree=None,
                                              objective='binary:logistic',
                                              random_state=None, ...)),
                             ('cat',
                              <catboost.core.CatBoostClassifier object at 0x171c42d60>),
                             ('gbc',
                              GradientBoostingClassifier(learning_rate=0.2,
                                                         n_estimators=200))],
                 voting='soft')

In [ ]:
cat.fit(X_train,y_train)

0:	learn: 0.6396279	total: 666ms	remaining: 3m 19s
1:	learn: 0.5939082	total: 989ms	remaining: 2m 27s
2:	learn: 0.5517480	total: 1.32s	remaining: 2m 11s
3:	learn: 0.5140833	total: 1.67s	remaining: 2m 3s
4:	learn: 0.4799652	total: 1.97s	remaining: 1m 55s
5:	learn: 0.4493554	total: 2.27s	remaining: 1m 51s
6:	learn: 0.4222232	total: 2.69s	remaining: 1m 52s
7:	learn: 0.3958191	total: 3.02s	remaining: 1m 50s
8:	learn: 0.3731277	total: 3.37s	remaining: 1m 49s
9:	learn: 0.3513430	total: 3.71s	remaining: 1m 47s
10:	learn: 0.3312332	total: 4.02s	remaining: 1m 45s
11:	learn: 0.3165642	total: 4.33s	remaining: 1m 43s
12:	learn: 0.3002061	total: 4.76s	remaining: 1m 45s
13:	learn: 0.2840361	total: 4.99s	remaining: 1m 42s
14:	learn: 0.2703220	total: 5.32s	remaining: 1m 41s
15:	learn: 0.2574510	total: 5.65s	remaining: 1m 40s
16:	learn: 0.2459971	total: 5.92s	remaining: 1m 38s
17:	learn: 0.2341754	total: 6.18s	remaining: 1m 36s
18:	learn: 0.2232166	total: 6.52s	remaining: 1m 36s
19:	learn: 0.2133288	to

In [ ]:
cat.score(X_val,y_val)

0.5789473684210527

In [ ]:
best_lgt.score(X_train,y_train)

0.837730870712401

In [ ]:
best_lgt.score(X_val,y_val)

0.5368421052631579

In [ ]:
ensemble_model.score(X_train,y_train)

1.0

In [ ]:
ensemble_model.score(X_val,y_val)

0.5631578947368421

In [ ]:
best_lgt.score(X_val,y_val)

0.5368421052631579

In [ ]:
best_xgbm.score(X_val,y_val)

0.48947368421052634

In [645]:
best_cat.score(X_train,y_train)

0.8073878627968337

In [646]:
best_cat.score(X_val,y_val)

0.6105263157894737

In [ ]:
best_cat.get_params()

{'iterations': 100, 'learning_rate': 0.01, 'depth': 7}

In [ ]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2', 'labels'],
      dtype='object')

In [670]:
best_cat.save_model("catboost.cbm")

In [666]:
feature_importance = pd.DataFrame({'feat_name':columns, 'model_feat_imp_train':loaded_model.feature_importances_}).sort_values(by='model_feat_imp_train', ascending=False).reset_index(drop=True)

In [667]:
feature_importance

feat_name model_feat_imp_train
0     team_count_50runs_last15                 None
1              team_winp_last5                 None
2    team1only_avg_runs_last15                 None
3      team1_winp_team2_last15                 None
4       ground_avg_runs_last15                 None
5    team2only_avg_runs_last15                 None
6     ratio_team12_strike_rate                 None
7           economy_team_ratio                 None
8             boundaries_ratio                 None
9             team2_winp_last5                 None
10          toss_win_match_win                 None
11                 field_ratio                 None
12     weighted_avg_runs_ratio                 None
13  weighted_avg_wickets_ratio                 None
14                win_by_team1                 None
15                win_by_team2                 None

In [ ]:
from sklearn.metrics import classification_report

In [ ]:
print(classification_report(y_true=y_val,y_pred=best_cat.predict(X_val)))

              precision    recall  f1-score   support

           0       0.62      0.64      0.63       103
           1       0.56      0.54      0.55        87

    accuracy                           0.59       190
   macro avg       0.59      0.59      0.59       190
weighted avg       0.59      0.59      0.59       190



Work over test dataset

In [744]:
test = pd.read_csv('R2Data.csv')

In [745]:
len(test)

207

In [746]:
test.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'toss winner', 'toss decision', 'venue',
       'city', 'match_dt', 'lighting', 'series_name', 'season', 'ground_id',
       'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15'],
      dtype='object')

In [747]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 207 entries, 0 to 206
Data columns (total 21 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   match id                   207 non-null    int64  
 1   team1                      207 non-null    object 
 2   team1_id                   207 non-null    int64  
 3   team1_roster_ids           207 non-null    object 
 4   team2                      207 non-null    object 
 5   team2_id                   207 non-null    int64  
 6   team2_roster_ids           207 non-null    object 
 7   toss winner                207 non-null    object 
 8   toss decision              207 non-null    object 
 9   venue                      207 non-null    object 
 10  city                       207 non-null    object 
 11  match_dt                   207 non-null    object 
 12  lighting                   207 non-null    object 
 13  series_name                207 non-null    object 

In [748]:
test.head()

match id  team1  team1_id  \
0   9272619  Me Ss     33949   
1   9086958     Na       209   
2   9433654     Gn      7573   
3   9097248     Ks     22784   
4   9097234     Ws     23841   

                                    team1_roster_ids  team2  team2_id  \
0  4003390.0:7960994.0:3901078.0:2669316.0:373710...  Ht Hs     33928   
1  5836452.0:8246468.0:7500324.0:3065502.0:363350...  Si La        69   
2  5164844.0:8110185.0:2979857.0:1722048.0:270743...     St      9701   
3  3496933.0:4167673.0:4160316.0:1863889.0:310883...     Ds     22763   
4  4166882.0:3009215.0:1963443.0:3252927.0:417185...     Ts     23750   

                                    team2_roster_ids toss winner  \
0  5843200.0:4223883.0:4655384.0:6249256.0:216159...       Ht Hs   
1  7200598.0:4403531.0:3260564.0:2420760.0:239834...       Si La   
2  6139370.0:7694581.0:3294444.0:3239102.0:481700...          St   
3  3399745.0:4898074.0:3782225.0:2252452.0:223190...          Ks   
4  2654014.0:2667223.0:3406717.0:3057312.0:415964...          Ts   

  toss decision           venue  ...    match_dt         lighting  \
0         field        Be Ol Ht  ...  2023-01-09      night match   
1         field  GA Sm Sh Gg Va  ...  2022-10-16  day/night match   
2         field        Sa Gs Cf  ...  2023-06-21  day/night match   
3           bat  St Gs Pk Pt Eh  ...  2022-02-08        day match   
4         field  St Gs Pk Pt Eh  ...  2022-02-07        day match   

      series_name   season ground_id  team_count_50runs_last15  \
0        Bg Bh Le  2022/23      6348                  0.666667   
1  Si La tr of Aa  2022/23      3961                  0.142857   
2           Vy Bt     2023      4521                  0.666667   
3        CA T0 Ce  2021/22      1224                  0.500000   
4        CA T0 Ce  2021/22      1224                  0.166667   

   team_winp_last5  team1only_avg_runs_last15  team1_winp_team2_last15  \
0         1.000000                 167.933333                     60.0   
1         0.207921                 141.888889                      0.0   
2         0.344262                 178.800000                      0.0   
3         0.259259                 138.000000                      0.0   
4         1.000000                 155.800000                    100.0   

   ground_avg_runs_last15  
0              154.115385  
1              142.833333  
2              155.733333  
3              142.500000  
4                     NaN  

[5 rows x 21 columns]

In [749]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 42 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   match id                    948 non-null    int64  
 1   team1                       948 non-null    object 
 2   team1_id                    948 non-null    int64  
 3   team1_roster_ids            948 non-null    object 
 4   team2                       948 non-null    object 
 5   team2_id                    948 non-null    int64  
 6   team2_roster_ids            948 non-null    object 
 7   winner                      948 non-null    object 
 8   winner_id                   948 non-null    int64  
 9   toss winner                 948 non-null    object 
 10  toss decision               948 non-null    object 
 11  venue                       948 non-null    object 
 12  city                        948 non-null    object 
 13  match_dt                    948 non

In [750]:
submission = pd.read_csv('/Users/palswayam5/Desktop/Amex Superbowl/Submission.csv')

In [751]:
submission.head()

match id dataset_type  win_pred_team_id  win_pred_score  train_algorithm  \
0   9272619           r2               NaN             NaN              NaN   
1   9086958           r2               NaN             NaN              NaN   
2   9433654           r2               NaN             NaN              NaN   
3   9097248           r2               NaN             NaN              NaN   
4   9097234           r2               NaN             NaN              NaN   

   is_ensemble  train_hps_trees  train_hps_depth  train_hps_lr  \
0          NaN              NaN              NaN           NaN   
1          NaN              NaN              NaN           NaN   
2          NaN              NaN              NaN           NaN   
3          NaN              NaN              NaN           NaN   
4          NaN              NaN              NaN           NaN   

   indep_feat_id1  indep_feat_id2  indep_feat_id3  indep_feat_id4  \
0             NaN             NaN             NaN             NaN   
1             NaN             NaN             NaN             NaN   
2             NaN             NaN             NaN             NaN   
3             NaN             NaN             NaN             NaN   
4             NaN             NaN             NaN             NaN   

   indep_feat_id5  indep_feat_id6  indep_feat_id7  indep_feat_id8  \
0             NaN             NaN             NaN             NaN   
1             NaN             NaN             NaN             NaN   
2             NaN             NaN             NaN             NaN   
3             NaN             NaN             NaN             NaN   
4             NaN             NaN             NaN             NaN   

   indep_feat_id9  indep_feat_id10  
0             NaN              NaN  
1             NaN              NaN  
2             NaN              NaN  
3             NaN              NaN  
4             NaN              NaN

In [752]:
submission['dataset_type'].value_counts()

dataset_type
r2    207
Name: count, dtype: int64

In [753]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2', 'labels',
       'dataset_type', 'y_pred_01', 'win_pred_score', 'win_pred_team_id'],
      dtype='object')

In [754]:
test['team1only_avg_runs_last15'].fillna(test['team1only_avg_runs_last15'].mean(),inplace=True)
test['ground_avg_runs_last15'].fillna(test['ground_avg_runs_last15'].mean(),inplace=True)

/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/2886168356.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  test['team1only_avg_runs_last15'].fillna(test['team1only_avg_runs_last15'].mean(),inplace=True)
/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/2886168356.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermed

In [755]:
test['team2only_avg_runs_last15'] = test.progress_apply(lambda x:team2AvgRunsLastn(x['team2_id'], x['match_dt'], 15), axis=1)

100%|██████████| 207/207 [00:00<00:00, 852.12it/s]


In [756]:
test['team1_avg_strike_rate'] = test.progress_apply(lambda x:avgStrikeRate(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['team2_avg_strike_rate'] = test.progress_apply(lambda x:avgStrikeRate(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

  0%|          | 0/207 [00:00<?, ?it/s]

/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:10: RuntimeWarning: Mean of empty slice
  res_list.append(np.nanmean(df_player['strike_rate']))
  0%|          | 0/207 [00:00<?, ?it/s]/var/folders/tb/vkjk1d1x5hqfpl49c_70mv840000gn/T/ipykernel_28352/199865680.py:10: RuntimeWarning: Mean of empty slice
  res_list.append(np.nanmean(df_player['strike_rate']))
100%|██████████| 207/207 [00:02<00:00, 87.69it/s]


In [757]:
test['ratio_team12_strike_rate'] = (1+test['team1_avg_strike_rate'])/(1+test['team2_avg_strike_rate'])
test.drop(['team1_avg_strike_rate','team2_avg_strike_rate'],axis = 1,inplace = True)

In [758]:
test['wicket_team1'] = test.progress_apply(lambda x:wickets(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['wicket_team2'] = test.progress_apply(lambda x:wickets(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:01<00:00, 111.05it/s]


In [759]:
test['wicket_team_ratio'] = (1+test['wicket_team1'])/(1+test['wicket_team2'])
test.drop(['wicket_team1','wicket_team2'],axis = 1,inplace = True)

In [760]:
test['economy_team1'] = test.progress_apply(lambda x:economy_7_halls(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['economy_team2'] = test.progress_apply(lambda x:economy_7_halls(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:02<00:00, 92.67it/s]


In [761]:
test['economy_team_ratio'] = (1+test['economy_team1'])/(1+test['economy_team2'])
test.drop(['economy_team1','economy_team2'],axis = 1,inplace=True)


In [762]:
test['wides_team1'] =  test.progress_apply(lambda x:wides(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['wides_team2'] =  test.progress_apply(lambda x:wides(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:01<00:00, 106.47it/s]


In [763]:
test['wides'] = (1+test['wides_team1'])/(1+test['wides_team2'])
test.drop(['wides_team1','wides_team2'],axis = 1,inplace=True)

In [764]:
test['noballs_team1'] =  test.progress_apply(lambda x:No_balls(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['noballs_team2'] =  test.progress_apply(lambda x:No_balls(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:01<00:00, 110.88it/s]


In [765]:
test['noballs_ratio'] = (1+test['noballs_team1'])/(1+test['noballs_team2'])
test.drop(['noballs_team1','noballs_team2'],axis = 1,inplace=True)

In [766]:
test['fours_team1'] = test.progress_apply(lambda x:count_of_fours(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['fours_team2'] = test.progress_apply(lambda x:count_of_fours(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

test['six_team1'] = test.progress_apply(lambda x:count_of_sixes(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['six_team2'] = test.progress_apply(lambda x:count_of_sixes(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:02<00:00, 86.04it/s]


In [767]:
test['boundaries_ratio'] = (1+test['fours_team1']+test['six_team1'])/(1+test['fours_team2']+test['six_team2'])
test.drop(['fours_team1','fours_team2','six_team1','six_team2'],axis = 1,inplace = True)

In [768]:
test['team2only_avg_runs_last15'] = test['team2only_avg_runs_last15'].fillna(np.mean(test['team2only_avg_runs_last15']))
test['ratio_team12_strike_rate'] = test['ratio_team12_strike_rate'].fillna(np.mean(test['ratio_team12_strike_rate']))

In [769]:
test['team2_winp_last5'] = test.progress_apply(lambda x:winpLastn(x['team1_id'],x['match_dt'],5),axis = 1)

100%|██████████| 207/207 [00:00<00:00, 1706.11it/s]


In [770]:
test.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'toss winner', 'toss decision', 'venue',
       'city', 'match_dt', 'lighting', 'series_name', 'season', 'ground_id',
       'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5'],
      dtype='object')

In [771]:
test['toss_win_match_win'] = test.progress_apply(lambda x:toss(x['match id'],x['toss winner'],test),axis = 1)

100%|██████████| 207/207 [00:00<00:00, 5094.03it/s]


In [772]:
test['field_team1'] = test.progress_apply(lambda x:fielding_capapbilty(x['team1_id'],x['match_dt'],Last_n_matches),axis = 1)
test['field_team2'] = test.progress_apply(lambda x:fielding_capapbilty(x['team2_id'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:05<00:00, 39.51it/s]


In [773]:
test['field_ratio'] = (1+test['field_team1'])/(1+test['field_team2'])
test.drop(['field_team1','field_team2'],axis = 1,inplace = True)

In [774]:
test['weighted_runs_team1'] = test.progress_apply(lambda x:weighted_Avg_runs(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['weighted_runs_team2'] = test.progress_apply(lambda x:weighted_Avg_runs(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:02<00:00, 80.86it/s]


In [775]:
test['weighted_avg_runs_ratio'] = (1+test['weighted_runs_team1'])/(1+test['weighted_runs_team2'])
test.drop(['weighted_runs_team1','weighted_runs_team2'],axis = 1,inplace = True)

In [776]:
test['weighted_wickets_team1'] = test.progress_apply(lambda x:weighted_Avg_wickets(x['team1_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)
test['weighted_wickets_team2'] = test.progress_apply(lambda x:weighted_Avg_wickets(x['team2_roster_ids'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:02<00:00, 96.65it/s] 


In [777]:
test['weighted_avg_wickets_ratio'] = (1+test['weighted_wickets_team1'])/(1+test['weighted_wickets_team2'])
test.drop(['weighted_wickets_team1','weighted_wickets_team2'],axis = 1,inplace = True)

In [778]:
test['win_by_team1'] = test.progress_apply(lambda x:ratio_of_wins(x['team1_id'],x['match_dt'],Last_n_matches),axis = 1)
test['win_by_team2'] = test.progress_apply(lambda x:ratio_of_wins(x['team2_id'],x['match_dt'],Last_n_matches),axis = 1)

100%|██████████| 207/207 [00:00<00:00, 1840.90it/s]


In [779]:
train.describe()

match id      team1_id      team2_id     winner_id     ground_id  \
count  9.480000e+02    948.000000    948.000000    948.000000    948.000000   
mean   9.323234e+06  21921.722574  21768.040084  21722.776371   7163.773207   
std    2.302622e+05  17657.672717  17555.597707  17596.249007   6932.193437   
min    8.797053e+06     20.000000     20.000000     20.000000     83.000000   
25%    9.097078e+06   6838.000000   7258.000000   7258.000000   1378.000000   
50%    9.330600e+06  18360.000000  17982.000000  17863.000000   4661.000000   
75%    9.484520e+06  36126.000000  36126.000000  36112.000000  11892.000000   
max    9.887863e+06  49657.000000  49657.000000  49657.000000  25479.000000   

       team_count_50runs_last15  team_winp_last5  team1only_avg_runs_last15  \
count                948.000000       948.000000                 948.000000   
mean                   1.202602         4.904243                 161.578491   
std                    1.008793        15.839620                  14.288634   
min                    0.083333         0.009901                 103.000000   
25%                    0.686678         0.603960                 153.525000   
50%                    1.000000         1.000000                 162.775000   
75%                    1.400000         1.952381                 171.088942   
max                   11.000000       101.000000                 218.500000   

       team1_winp_team2_last15  ground_avg_runs_last15  ...  \
count               948.000000              948.000000  ...   
mean                 40.991561              153.822446  ...   
std                  37.948831               13.575032  ...   
min                   0.000000               81.500000  ...   
25%                   0.000000              146.166667  ...   
50%                  40.000000              153.822446  ...   
75%                  66.670000              162.000000  ...   
max                 100.000000              209.500000  ...   

       toss_win_match_win  field_ratio  weighted_avg_runs_ratio  \
count          948.000000   948.000000               948.000000   
mean             0.650844     1.622966                 1.316261   
std              0.476955     5.068559                 1.146240   
min              0.000000     0.015385                 0.080593   
25%              0.000000     0.854544                 0.624348   
50%              1.000000     1.000000                 1.024252   
75%              1.000000     1.203563                 1.640510   
max              1.000000    82.000000                13.280267   

       weighted_avg_wickets_ratio  win_by_team1  win_by_team2      labels  \
count                  948.000000    948.000000    948.000000  948.000000   
mean                     1.036762      1.203721      1.225698    0.503165   
std                      0.266694      0.767625      0.811587    0.500254   
min                      0.330648      0.142857      0.125000    0.000000   
25%                      0.926179      0.700000      0.700000    0.000000   
50%                      1.000869      1.000000      1.000000    1.000000   
75%                      1.095140      1.428571      1.428571    1.000000   
max                      2.865261      7.500000      7.500000    1.000000   

        y_pred_01  win_pred_score  win_pred_team_id  
count  948.000000      948.000000        948.000000  
mean     0.473629        0.593783      21636.199367  
std      0.499568        0.071758      17507.875568  
min      0.000000        0.500144         20.000000  
25%      0.000000        0.538815       7258.000000  
50%      0.000000        0.577328      17744.000000  
75%      1.000000        0.638271      36098.000000  
max      1.000000        0.840695      49657.000000  

[8 rows x 28 columns]

In [780]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 207 entries, 0 to 206
Data columns (total 35 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   match id                    207 non-null    int64  
 1   team1                       207 non-null    object 
 2   team1_id                    207 non-null    int64  
 3   team1_roster_ids            207 non-null    object 
 4   team2                       207 non-null    object 
 5   team2_id                    207 non-null    int64  
 6   team2_roster_ids            207 non-null    object 
 7   toss winner                 207 non-null    object 
 8   toss decision               207 non-null    object 
 9   venue                       207 non-null    object 
 10  city                        207 non-null    object 
 11  match_dt                    207 non-null    object 
 12  lighting                    207 non-null    object 
 13  series_name                 207 non

In [781]:
test.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'toss winner', 'toss decision', 'venue',
       'city', 'match_dt', 'lighting', 'series_name', 'season', 'ground_id',
       'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2'],
      dtype='object')

In [782]:
X_test = test.drop(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'toss winner', 'toss decision', 'venue',
       'city', 'match_dt', 'lighting', 'series_name', 'season', 'ground_id','wicket_team_ratio','wides', 'noballs_ratio'],axis = 1)

In [783]:
X_test

team_count_50runs_last15  team_winp_last5  team1only_avg_runs_last15  \
0                    0.666667         1.000000                 167.933333   
1                    0.142857         0.207921                 141.888889   
2                    0.666667         0.344262                 178.800000   
3                    0.500000         0.259259                 138.000000   
4                    0.166667         1.000000                 155.800000   
..                        ...              ...                        ...   
202                  0.307692         1.952381                 181.400000   
203                  0.857143         0.344262                 189.133333   
204                  1.368421         0.672131                 185.666667   
205                  0.736842         0.344262                 189.133333   
206                  1.000000         0.344262                 189.133333   

     team1_winp_team2_last15  ground_avg_runs_last15  \
0                       60.0              154.115385   
1                        0.0              142.833333   
2                        0.0              155.733333   
3                        0.0              142.500000   
4                      100.0              157.888017   
..                       ...                     ...   
202                     50.0              181.625000   
203                     40.0              168.033333   
204                     75.0              168.033333   
205                     50.0              157.933333   
206                     40.0              157.933333   

     team2only_avg_runs_last15  ratio_team12_strike_rate  economy_team_ratio  \
0                   158.733333                  0.792694            1.789474   
1                   153.933333                  0.832030            0.750000   
2                   148.600000                  0.810790            0.684211   
3                   129.333333                  0.964565            1.250000   
4                   124.400000                  1.154437            0.625000   
..                         ...                       ...                 ...   
202                 173.800000                  0.963126            0.896552   
203                 160.733333                  1.104421            0.674419   
204                 163.600000                  0.892223            1.108108   
205                 163.600000                  1.075923            0.918919   
206                 160.733333                  1.139296            0.790698   

     boundaries_ratio  team2_winp_last5  toss_win_match_win  field_ratio  \
0            0.633218              40.0                   1     0.985714   
1            0.330000              20.0                   1     0.586207   
2            0.691395              20.0                   1     1.013514   
3            1.058824              20.0                   0     0.769231   
4            0.578947              40.0                   1     1.040000   
..                ...               ...                 ...          ...   
202          0.700315              40.0                   0     1.014925   
203          1.060201              20.0                   0     1.080645   
204          1.221622              40.0                   1     0.900000   
205          0.967568              20.0                   1     0.957143   
206          1.197324              20.0                   0     1.080645   

     weighted_avg_runs_ratio  weighted_avg_wickets_ratio  win_by_team1  \
0                   0.451539                    1.007308      1.428571   
1                   0.919262                    1.003033      0.571429   
2                   0.501411                    1.158151      1.428571   
3                   1.073722                    0.827292      0.400000   
4                   0.943614                    0.813797      2.500000   
..                       ...                         ...           ...   
202            

In [ ]:
#X_test = (X_test-X_test.mean())/(X_test.max() - X_test.min())

In [784]:
train_copy['dataset_type'] = 'train'
test['dataset_type'] = 'r2'

In [785]:
X.shape,X_test.shape

((948, 16), (207, 16))

In [786]:
train_copy['y_pred_01'] = best_cat.predict(X)
test['y_pred_01'] = best_cat.predict(X_test)

In [787]:
train_copy['win_pred_score'] = best_cat.predict_proba(X)[:,1]
test['win_pred_score'] = best_cat.predict_proba(X_test)[:,1]

In [788]:
train.head(2)

match id team1  team1_id  \
0   9331181    Ba     11283   
1   8797060    Ed        20   

                                    team1_roster_ids  team2  team2_id  \
0  9373356.0:7857520.0:4232164.0:4566540.0:329940...  Hl Ph     12634   
1  2089079.0:6139370.0:2076192.0:62432.0:2083409....  Wt Is        41   

                                    team2_roster_ids winner  winner_id  \
0  3500958.0:4231751.0:2735081.0:2035102.0:369833...  Hl Ph      12634   
1  4690258.0:4069666.0:4230127.0:1942317.0:161392...     Ed         20   

  toss winner  ... field_ratio weighted_avg_runs_ratio  \
0       Hl Ph  ...    1.578947                3.715559   
1       Wt Is  ...    0.791045                0.388574   

  weighted_avg_wickets_ratio win_by_team1 win_by_team2 labels dataset_type  \
0                   0.330648          0.7     0.857143      1        train   
1                   1.548832          0.7     1.833333      0        train   

   y_pred_01  win_pred_score  win_pred_team_id  
0          0        0.316308             11283  
1          0        0.367910                20  

[2 rows x 42 columns]

In [789]:
train_copy['win_pred_score'] = np.where( (train_copy['y_pred_01']==0), (1-train_copy['win_pred_score']), train_copy['win_pred_score'])
test['win_pred_score'] = np.where( (test['y_pred_01']==0), (1-test['win_pred_score']), test['win_pred_score'])

In [790]:
test.head(2)

match id  team1  team1_id  \
0   9272619  Me Ss     33949   
1   9086958     Na       209   

                                    team1_roster_ids  team2  team2_id  \
0  4003390.0:7960994.0:3901078.0:2669316.0:373710...  Ht Hs     33928   
1  5836452.0:8246468.0:7500324.0:3065502.0:363350...  Si La        69   

                                    team2_roster_ids toss winner  \
0  5843200.0:4223883.0:4655384.0:6249256.0:216159...       Ht Hs   
1  7200598.0:4403531.0:3260564.0:2420760.0:239834...       Si La   

  toss decision           venue  ... team2_winp_last5 toss_win_match_win  \
0         field        Be Ol Ht  ...             40.0                  1   
1         field  GA Sm Sh Gg Va  ...             20.0                  1   

  field_ratio weighted_avg_runs_ratio weighted_avg_wickets_ratio  \
0    0.985714                0.451539                   1.007308   
1    0.586207                0.919262                   1.003033   

   win_by_team1  win_by_team2  dataset_type  y_pred_01  win_pred_score  
0      1.428571      3.250000            r2          1         0.59321  
1      0.571429      0.545455            r2          1         0.59797  

[2 rows x 38 columns]

In [791]:
train_copy['win_pred_team_id'] = np.where( (train_copy['y_pred_01']==0), (train_copy['team1_id']), train_copy['team2_id'])
test['win_pred_team_id'] = np.where( (test['y_pred_01']==0), (test['team1_id']), test['team2_id'])

In [792]:
df21_submission = pd.concat([test[['match id','dataset_type','win_pred_team_id','win_pred_score',] + list(feature_importance['feat_name'].head(10))]])

In [793]:
df21_submission.head(2)

match id dataset_type  win_pred_team_id  win_pred_score  \
0   9272619           r2             33928         0.59321   
1   9086958           r2                69         0.59797   

   team_count_50runs_last15  team_winp_last5  team1only_avg_runs_last15  \
0                  0.666667         1.000000                 167.933333   
1                  0.142857         0.207921                 141.888889   

   team1_winp_team2_last15  ground_avg_runs_last15  team2only_avg_runs_last15  \
0                     60.0              154.115385                 158.733333   
1                      0.0              142.833333                 153.933333   

   ratio_team12_strike_rate  economy_team_ratio  boundaries_ratio  \
0                  0.792694            1.789474          0.633218   
1                  0.832030            0.750000          0.330000   

   team2_winp_last5  
0              40.0  
1              20.0

In [794]:
best_cat.get_params()

{'iterations': 300, 'learning_rate': 0.01, 'depth': 5}

In [ ]:
#algo_name = 'lightbgm;catboost;xgboost'
#is_ensemble = 'yes'
#n_trees = ';'.join([str(best_lgt.get_params()['n_estimators']),str(best_cat.get_params()['iterations']),str(best_xgbm.get_params()['n_estimators'])])
#depth = ';'.join([str(best_lgt.get_params()['max_depth']),str(best_cat.get_params()['depth']),str(best_xgbm.get_params()['max_depth'])])
#lr = ';'.join([str(best_lgt.get_params()['learning_rate']),str(best_cat.get_params()['learning_rate']),str(best_xgbm.get_params()['learning_rate'])])

In [795]:
algo_name = 'catboost'
is_ensemble = 'no'
n_trees = best_cat.get_params()['iterations']
depth = best_cat.get_params()['depth']
lr = best_cat.get_params()['learning_rate']

In [796]:
renaming_dict = {}
for i,col in enumerate(list(feature_importance['feat_name'].head(10))):
    renaming_dict[col] = f'indep_feat_id{i+1}'
df21_submission.rename(columns=renaming_dict, inplace=True)

for i in range(1,11):
    if f'indep_feat_id{i}' not in df21_submission.columns:
        df21_submission[f'indep_feat_id{i}'] = np.nan

df21_submission['train_algorithm'] = algo_name
df21_submission['is_ensemble'] = is_ensemble
df21_submission['train_hps_trees'] = n_trees
df21_submission['train_hps_depth'] = depth
df21_submission['train_hps_lr'] = lr

In [797]:
df21_submission.head(5)

match id dataset_type  win_pred_team_id  win_pred_score  indep_feat_id1  \
0   9272619           r2             33928        0.593210        0.666667   
1   9086958           r2                69        0.597970        0.142857   
2   9433654           r2              9701        0.650364        0.666667   
3   9097248           r2             22763        0.559141        0.500000   
4   9097234           r2             23750        0.658635        0.166667   

   indep_feat_id2  indep_feat_id3  indep_feat_id4  indep_feat_id5  \
0        1.000000      167.933333            60.0      154.115385   
1        0.207921      141.888889             0.0      142.833333   
2        0.344262      178.800000             0.0      155.733333   
3        0.259259      138.000000             0.0      142.500000   
4        1.000000      155.800000           100.0      157.888017   

   indep_feat_id6  indep_feat_id7  indep_feat_id8  indep_feat_id9  \
0      158.733333        0.792694        1.789474        0.633218   
1      153.933333        0.832030        0.750000        0.330000   
2      148.600000        0.810790        0.684211        0.691395   
3      129.333333        0.964565        1.250000        1.058824   
4      124.400000        1.154437        0.625000        0.578947   

   indep_feat_id10 train_algorithm is_ensemble  train_hps_trees  \
0             40.0        catboost          no              300   
1             20.0        catboost          no              300   
2             20.0        catboost          no              300   
3             20.0        catboost          no              300   
4             40.0        catboost          no              300   

   train_hps_depth  train_hps_lr  
0                5          0.01  
1                5          0.01  
2                5          0.01  
3                5          0.01  
4                5          0.01

In [798]:
feature_importance['feat_name']

0       team_count_50runs_last15
1                team_winp_last5
2      team1only_avg_runs_last15
3        team1_winp_team2_last15
4         ground_avg_runs_last15
5      team2only_avg_runs_last15
6       ratio_team12_strike_rate
7             economy_team_ratio
8               boundaries_ratio
9               team2_winp_last5
10            toss_win_match_win
11                   field_ratio
12       weighted_avg_runs_ratio
13    weighted_avg_wickets_ratio
14                  win_by_team1
15                  win_by_team2
Name: feat_name, dtype: object

In [799]:
feature_desc = {
    'team2only_avg_runs_last15':'average runs scored by team 2 in last 15 matches',
    'ground_avg_runs_last15':'average runs scored on that ground in last 15 matches',
    'ratio_team12_strike_rate':'ratio of average strike rate all the players of team1 to team2',
    'team_count_50runs_last15':'ratio of numbers of 50s of players of team1 to team2',
    'wicket_team_ratio':'ratio of total wickets taken by team1 to team2',
    'economy_team_ratio':'ratio of total less than 7 economy halls taken by team1 to team2',
    'boundaries_ratio':'total boundaries scoerd by team1 to team2',
    'team1only_avg_runs_last15':'average runs scored by team 1 in last 15 matches',
    'team_winp_last5':'team1 win probability in last 5 matches',
    'wides':'ratio of total wides taken by team1 to team2',
    'noballs_ratio':'ratio of total noballs taken by team1 to team2',
    'team2_winp_last5':'team2 win probability in last 5 matches',
    'team1_winp_team2_last15':'ratio of team1 winp against team2 in alst 15 matches',
    'toss_win_match_win':'if team 1 wins the toss then the value is 0 else 1',
    'field_ratio':'fielding capabilities ratio',
    'weighted_avg_runs_ratio':'weighted average runs ratio',
    'weighted_avg_wickets_ratio':'wighted average wicket ratio',
    'win_by_team1':'ratio of win by wickets to runs of team 1',
    'win_by_team2':'ratio of win by wickets to runs of team 2'
}

In [ ]:
df_file2 = feature_importance
df_file2['feat_id'] = [i+1 for i in df_file2.index]
df_file2['feat_rank_train'] = [i+1 for i in df_file2.index]
df_file2 = df_file2.set_index('feat_id')
df_file2['feat_description'] = df_file2['feat_name'].map(feature_desc)

In [ ]:
df_file2['model_feat_imp_train'] = df_file2['model_feat_imp_train'].astype('float')

In [ ]:
df_file2.head(14)

feat_name  model_feat_imp_train  feat_rank_train  \
feat_id                                                                      
1                economy_team_ratio             11.569194                1   
2                  boundaries_ratio              9.304721                2   
3         team2only_avg_runs_last15              9.195468                3   
4          ratio_team12_strike_rate              8.614617                4   
5        weighted_avg_wickets_ratio              7.838430                5   
6          team_count_50runs_last15              7.661554                6   
7                       field_ratio              7.554644                7   
8         team1only_avg_runs_last15              6.418891                8   
9            ground_avg_runs_last15              6.331664                9   
10                  team_winp_last5              6.115076               10   
11          team1_winp_team2_last15              5.940005               11   
12                 team2_winp_last5              5.577539               12   
13          weighted_avg_runs_ratio              4.731397               13   
14               toss_win_match_win              3.146800               14   

                                          feat_description  
feat_id                                                     
1        ratio of total less than 7 economy halls taken...  
2                total boundaries scoerd by team1 to team2  
3         average runs scored by team 2 in last 15 matches  
4        ratio of average strike rate all the players o...  
5                             wighted average wicket ratio  
6        ratio of numbers of 50s of players of team1 to...  
7                              fielding capabilities ratio  
8         average runs scored by team 1 in last 15 matches  
9        average runs scored on that ground in last 15 ...  
10                 team1 win probability in last 5 matches  
11       ratio of team1 winp against team2 in alst 15 m...  
12                 team2 win probability in last 5 matches  
13                             weighted average runs ratio  
14       if team 1 wins the toss then the value is 0 el...

In [ ]:
train.columns

Index(['match id', 'team1', 'team1_id', 'team1_roster_ids', 'team2',
       'team2_id', 'team2_roster_ids', 'winner', 'winner_id', 'toss winner',
       'toss decision', 'venue', 'city', 'match_dt', 'lighting', 'series_name',
       'season', 'ground_id', 'team_count_50runs_last15', 'team_winp_last5',
       'team1only_avg_runs_last15', 'team1_winp_team2_last15',
       'ground_avg_runs_last15', 'team2only_avg_runs_last15',
       'ratio_team12_strike_rate', 'wicket_team_ratio', 'economy_team_ratio',
       'wides', 'noballs_ratio', 'boundaries_ratio', 'team2_winp_last5',
       'toss_win_match_win', 'field_ratio', 'weighted_avg_runs_ratio',
       'weighted_avg_wickets_ratio', 'win_by_team1', 'win_by_team2', 'labels',
       'dataset_type', 'y_pred_01', 'win_pred_score', 'win_pred_team_id'],
      dtype='object')

In [800]:
df22_submission = df21_submission[['match id','dataset_type','win_pred_team_id']]

In [801]:
df21_submission.to_csv('round_2_submission1.csv', index=False)
df22_submission.to_csv('round_2_submission2.csv')

In [802]:
df21_submission.columns

Index(['match id', 'dataset_type', 'win_pred_team_id', 'win_pred_score',
       'indep_feat_id1', 'indep_feat_id2', 'indep_feat_id3', 'indep_feat_id4',
       'indep_feat_id5', 'indep_feat_id6', 'indep_feat_id7', 'indep_feat_id8',
       'indep_feat_id9', 'indep_feat_id10', 'train_algorithm', 'is_ensemble',
       'train_hps_trees', 'train_hps_depth', 'train_hps_lr'],
      dtype='object')